## Homework 7.0: BBC Movie List Scraping and Regex

In 2016 the BBC polled 177 film critics to get their picks for the best films of the century so far. While the BBC's [aggregate poll](http://www.bbc.com/culture/story/20160819-the-21st-centurys-100-greatest-films) is interesting, the long list including everyone who voted is perhaps more revealing from the data standpoint:

https://www.bbc.com/culture/article/20160819-the-21st-centurys-100-greatest-films-who-voted

How do I wrangle this data? That is the central challenge that you'll be dealing with this week. You need to use beautiful soup to find the critic--as well as the list of movies that immediately follow them—and then use regular expression to divide the critic information and the movie info to create the most useful possible data structure. What should the data structure be? That is up to you to figure out.



### Getting started: Data Architecture

The central challenge of this assignment it's figuring out how you are going to set up your table (list of dictionaries) from this long list of critics and movies. What will each row be? What will the columns be and each row? How can you set it up so that you have the most useful table possible. 

Some things to think about: what are the main categories of analysis: Try to design a schema that will give you a table that you can run solid aggregations in pandas. Try to think about how you can transform the main source into one large table that can be aggregated and grouped.

### STEP 1

The first thing you need to do is scrape the page. 

https://www.bbc.com/culture/article/20160819-the-21st-centurys-100-greatest-films-who-voted

Okay let's begin! (Note: I have set up the first few cells so that you can run requests once AND save the HTML page as a local file. And then load that local file in and do the spray thing on it. That way you only need to run requests once (ever)!)



In [1]:
##Import your libraries: Beautiful soup, requests, and re (For regular expressions)
import requests
from bs4 import BeautifulSoup
import re


In [2]:
#RUN THIS ONE TIME
#THEN COMMENT-OUT ALL OF THIS CODE
# my_url = "https://www.bbc.com/culture/article/20160819-the-21st-centurys-100-greatest-films-who-voted"
# raw_html = requests.get(my_url).content


In [3]:
#WRITING THE HTML FILE TO A LOCAL HTML FILE
#RUN THIS ONE TIME, THEN COMMENT-OUT ALL OF THIS CODE
# with open('bbc.html', 'wb+') as f:
#     f.write(raw_html)

In [4]:
#If you have run requests already--START HERE
f = open("bbc.html", "r")
local_html = f.read()
local_html

'<!DOCTYPE html><html lang="en-GB"><head><meta charSet="utf-8"/><meta name="viewport" content="width=device-width"/><title>The 21st Century’s 100 greatest films: Who voted?</title><meta property="og:title" content="The 21st Century’s 100 greatest films: Who voted?"/><meta name="twitter:title" content="The 21st Century’s 100 greatest films: Who voted?"/><meta name="description" content="We polled 177 critics from around the world – here is how they voted."/><meta property="og:description" content="We polled 177 critics from around the world – here is how they voted."/><meta name="twitter:description" content="We polled 177 critics from around the world – here is how they voted."/><meta property="og:image" content="https://ychef.files.bbci.co.uk/624x351/p04548r6.jpg"/><meta name="twitter:image:src" content="https://ychef.files.bbci.co.uk/624x351/p04548r6.jpg"/><meta name="twitter:card" content="summary_large_image"/><meta name="msapplication-TileColor" content="#da532c"/><meta name="them

In [5]:
# read the URL, and put the HTML page into beautiful soup

soup_doc = BeautifulSoup(local_html, "html.parser")
print(soup_doc.prettify())

<!DOCTYPE html>
<html lang="en-GB">
 <head>
  <meta charset="utf-8"/>
  <meta content="width=device-width" name="viewport"/>
  <title>
   The 21st Century’s 100 greatest films: Who voted?
  </title>
  <meta content="The 21st Century’s 100 greatest films: Who voted?" property="og:title"/>
  <meta content="The 21st Century’s 100 greatest films: Who voted?" name="twitter:title"/>
  <meta content="We polled 177 critics from around the world – here is how they voted." name="description"/>
  <meta content="We polled 177 critics from around the world – here is how they voted." property="og:description"/>
  <meta content="We polled 177 critics from around the world – here is how they voted." name="twitter:description"/>
  <meta content="https://ychef.files.bbci.co.uk/624x351/p04548r6.jpg" property="og:image"/>
  <meta content="https://ychef.files.bbci.co.uk/624x351/p04548r6.jpg" name="twitter:image:src"/>
  <meta content="summary_large_image" name="twitter:card"/>
  <meta content="#da532c" nam

In [6]:
#Using beautiful soup find the tag that contains 
#the entire list of critics and movies
#Make a variable (like full_list) that holds all that information 
full_list = soup_doc.article.find_all('p')


In [7]:
div_list = soup_doc.article.find_all('div')
len(div_list)

508

In [8]:
div_list[9]

<div class="sc-18fde0d6-0 dlWCEZ" data-component="text-block"><p class="sc-eb7bd5f6-0 fYAfXe"><b class="sc-7dcfb11b-0 kVRnKf" id="sam-adams-–-freelance-film-critic-(us)">Sam Adams – Freelance film critic (US)<!-- --></b></p></div>

In [9]:
allb = soup_doc.find_all('b')
len(allb)
for b in allb:
    print(b.text)

We polled 177 critics from around the world – here is how they voted.
Simon Abrams – Freelance film critic (US)
Sam Adams – Freelance film critic (US)
Thelma Adams – Freelance film critic (US)
Arturo Aguilar – Rolling Stone Mexico (Mexico)
Matthew Anderson – BBC Culture (UK)
Tim Appelo – The Wrap (US)
Adriano Aprà – Film historian (Italy)
Michael Arbeiter – Nerdist (US)
Ali Arikan – Dipnot TV (Turkey)
Michael Atkinson – The Village Voice (US)
Ana Maria Bahiana – Freelance film critic (Brazil)
Cameron Bailey – Toronto Film Festival (Canada)
Lindsay Baker – BBC Culture (UK)
Miriam Bale – Freelance film critic (US)
Nicholas Barber – BBC Culture (UK)
Diego Batlle – La Nacion (Argentina)
NT Binh – Positif (France)
Lizelle Bisschoff – University of Glasgow (UK)
Christian Blauvelt – BBC Culture (US)
Mahen Bonetti – African Film Festival Inc (US)
Andreas Borcholte – Spiegel Online (Germany)
Utpal Borpujari – Freelance film critic (India)
Richard Brody – The New Yorker (US)
Hannah Brown – Jerus

**STEP 2** Using Beautiful Soup figure out how to separate the entries.


In [10]:
full_list[2]
full_list[-9]
len(full_list)

1957

**STEP THREE** This is where all the magic has to happen: you need to find a way to loop through all of the elements (loop through the list you just got from the find_all()) and pullout critics, and list of movies. 

Set up a loop the PRINTS critics and movies: You need to set it up so that you're getting the critic string followed their movies. 

So just print out the lines along with a print message like "CRITIC" or "MOVIE" to make sure that the loop is recognizing the two categories differently.


In [11]:
##Write your loop for STEP 3 here


for entry in full_list[2:-8]:
    if entry.b:
        print(entry.text)
    else:
        print(entry.text)
        print("------------")


Simon Abrams – Freelance film critic (US)
1. Mulholland Drive (David Lynch, 2001)
------------
2. In the Mood for Love (Wong Kar-wai, 2000)
------------
3. The Tree of Life (Terrence Malick, 2011)
------------
4. Yi Yi: A One and a Two (Edward Yang, 2000)
------------
5. Goodbye to Language (Jean-Luc Godard, 2014)
------------
6. The White Meadows (Mohammad Rasoulof, 2009)
------------
7. Night Across the Street (Raoul Ruiz, 2012)
------------
8. Certified Copy (Abbas Kiarostami, 2010)
------------
9. Sparrow (Johnnie To, 2008)
------------
10. Fados (Carlos Saura, 2007)
------------
Sam Adams – Freelance film critic (US)
1. In the Mood for Love (Wong Kar-wai, 2000)
------------
2. Eternal Sunshine of the Spotless Mind (Michel Gondry, 2004)
------------
3. Syndromes and a Century (Apichatpong Weerasethakul, 2006)
------------
4. Spirited Away (Hayao Miyazaki, 2001)
------------
5. The Act of Killing (Joshua Oppenheimer, 2012)
------------
6. The Grand Budapest Hotel (Wes Anderson, 2014

**STEP 4**
If your loop is successfully isolating those two categories: now it's time to parse each with regular expressions (separately). This will need to happen inside the loop--for every critic, and then (in STEP 5) for every movie. But FIRST, just **focus on getting the critics name, organization, and country** in isolation (outside of the loops).

Once you have think you have your regular expressions working then bring them into a loop (just for CRITICS) and see how well they work.

Inside the loop--once you have critic_info -- make a regular expression that pulls out the name of the critic--make a variable called critic_name

`critic_name = findall(regex,critic_info)[0]`

Do the same thing for critic_org and critic_cn

As you go print(critic_name) then print(critic_org), etc.--to make sure you're getting the results. I provided a cell below for you to practice your regular expressions before you put them into the loop.

In [12]:
#Practice/Build your regular expressions here
import re
crit_sample = "Arturo Aguilar – Rolling Stone Mexico (Mexico)"
regex_for_name = r"^([^–]+)"
regex_for_org = r"–([^(]+)\("
regex_for_cn = r"\((.+)\)$"
name = re.findall(regex_for_cn,crit_sample)
name[0]


'Mexico'

In [13]:
#Take your working loop from step three
#And put it here With the regular expression parsing inside it
for entry in full_list[2:-8]:
    if entry.b:
        regex_for_name = r"^([^–]+)"
        regex_for_org = r"–([^(]+)\("
        regex_for_cn = r"\((.+)\)$"
        name = re.findall(regex_for_name,entry.text)[0]
        org = re.findall(regex_for_org,entry.text)[0]
        cn = re.findall(regex_for_cn,entry.text)[0]
        print(name + "|||" + org+ "|||"+ cn)


Simon Abrams ||| Freelance film critic |||US
Sam Adams ||| Freelance film critic |||US
Thelma Adams ||| Freelance film critic |||US
Arturo Aguilar ||| Rolling Stone Mexico |||Mexico
Matthew Anderson ||| BBC Culture |||UK
Tim Appelo ||| The Wrap |||US
Adriano Aprà ||| Film historian |||Italy
Michael Arbeiter ||| Nerdist |||US
Ali Arikan ||| Dipnot TV |||Turkey
Michael Atkinson ||| The Village Voice |||US
Ana Maria Bahiana ||| Freelance film critic |||Brazil
Cameron Bailey ||| Toronto Film Festival |||Canada
Lindsay Baker ||| BBC Culture |||UK
Miriam Bale ||| Freelance film critic |||US
Nicholas Barber ||| BBC Culture |||UK
Diego Batlle ||| La Nacion |||Argentina
NT Binh ||| Positif |||France
Lizelle Bisschoff ||| University of Glasgow |||UK
Christian Blauvelt ||| BBC Culture |||US
Mahen Bonetti ||| African Film Festival Inc |||US
Andreas Borcholte ||| Spiegel Online |||Germany
Utpal Borpujari ||| Freelance film critic |||India
Richard Brody ||| The New Yorker |||US
Hannah Brown ||| Jeru

**STEP 5**
Now you need to get your **movie info**. You will want to use the same loop you have been working on (in STEP 6), and get the name of each movie along with the critic information.

But **FIRST**: practice your regular expressions and make sure that they're going to work before you bring them into the loop.


In [14]:
#Practice/Build your regular expressions here
movie_sample = "1. Zero Dark Thirty (Kathryn Bigelow, 2012)"
movie_harder = "7. 4 Months, 3 Weeks & 2 Days (Cristian Mungiu, 2007)"
regex_for_mname = r"^\d{1,2}\. (.+)[(][^(]+[)]$"
regex_for_dir = r"\(([^(]+),\s+[^,(]+\)$"
regex_for_year = r",\s+(\d{4})\)$"
#what else should you extract???
#set up all regexes here
movie_name = re.findall(regex_for_year,movie_harder)
movie_name[0].strip()


'2007'

**STEP 6**
You're almost there!!! Now that you have working regulars expression put those in your inner loop to get the movie name.

So now the entire loop should be getting critic information and movie information all separated as separate columns/properties.

Build this loop(s) using print() on the first one or two critic selections. Just to make sure you are pulling out the right data.




In [15]:
#Get that loop working here

for entry in full_list[2:-8]:
    if entry.b:
        regex_for_name = r"^([^–]+)"
        regex_for_org = r"–([^(]+)\("
        regex_for_cn = r"\((.+)\)$"
        name = re.findall(regex_for_name,entry.text)[0]
        org = re.findall(regex_for_org,entry.text)[0]
        cn = re.findall(regex_for_cn,entry.text)[0]
        # print(name+ "|||" + org+ "|||"+cn)
    else:
        regex_for_mname = r"^\d{1,2}\. (.+)\([^(]+\)$"
        regex_for_dir = r"\(([^(]+),\s+[^,(]+\)$"
        regex_for_year = r",\s+([^,]+)\)$"
        # regex_for_multi_paren = r".+\(.+\("
        # regex_for_odddate = r", .{4}\)$"
        #what else should you extract???
        movie_name = re.findall(regex_for_mname,entry.text)[0]
        movie_dir = re.findall(regex_for_dir,entry.text)[0]
        movie_year = re.findall(regex_for_year,entry.text)[0]
        print(movie_name+ "|||" + movie_dir+ "|||"+movie_year)
        paren = re.findall(regex_for_odddate,entry.text)
        # if paren:
        #     print(paren)


        







Mulholland Drive |||David Lynch|||2001


NameError: name 'regex_for_odddate' is not defined

**STEP 7**
This is the final step of the hardest part! 

The final step is building a list of dictionaries of all this information.

So you need have a loop that gets everything out--but you also need to figure out **how  you want to organize what you're pulling out.** What should a row look like in your table?




In [16]:
#figure out how you're going to collect your clean information
list_of_movies = []

#loop through the beautiful soup elements
#and use the regexes you developed above to get each unit of info
for entry in full_list[2:-8]:
    if entry.b:
        regex_for_name = r"^([^–]+)"
        regex_for_org = r"–([^(]+)\("
        regex_for_cn = r"\((.+)\)$"
        name = re.findall(regex_for_name,entry.text)[0].strip()
        org = re.findall(regex_for_org,entry.text)[0].strip()
        cn = re.findall(regex_for_cn,entry.text)[0].strip()
        # print(name+ "|||" + org+ "|||"+cn)
    else:
        regex_for_mname = r"^\d{1,2}\. (.+)\([^(]+\)$"
        regex_for_dir = r"\(([^(]+),\s+[^,(]+\)$"
        regex_for_year = r",\s+([^,]+)\)$"
        regex_for_multi_paren = r".+\(.+\("
        #what else should you extract???
        movie_name = re.findall(regex_for_mname,entry.text)[0].strip()
        movie_dir = re.findall(regex_for_dir,entry.text)[0].strip()
        movie_year = re.findall(regex_for_year,entry.text)[0].strip()
        new_movie_entry = [movie_name,movie_dir,movie_year,name,org,cn]
        list_of_movies.append(new_movie_entry)
        

#Try to figure out how you want to append things
#That is, how you want to organize your data

    

In [17]:
##Take a peek at your final lists of lists
list_of_movies
len(list_of_movies)
list_of_movies[22:44]

[['The Grand Budapest Hotel',
  'Wes Anderson',
  '2014',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Stories We Tell',
  'Sarah Polley',
  '2012',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Casino Royale',
  'Martin Campbell',
  '2006',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Eternal Sunshine of the Spotless Mind',
  'Michel Gondry',
  '2004',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Tabu',
  'Miguel Gomes',
  '2012',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Snow White',
  'Pablo Berger',
  '2012',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Frozen River',
  'Courtney Hunt',
  '2008',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['Gosford Park',
  'Robert Altman',
  '2001',
  'Thelma Adams',
  'Freelance film critic',
  'US'],
 ['In the Mood for Love',
  'Wong Kar-wai',
  '2000',
  'Arturo Aguilar',
  'Rolling Stone Mexico',
  'Mexico'],
 ['Mulholland Drive',
  'David Lynch',
  '2001',
 

In [18]:
# for mov in list_of_movies:
#     if mov[1].startswith("Mool"):
#         print(mov)

for mov in list_of_movies:
    if re.search(r".+\d{4}",mov[2]):
        print(mov[2])

Sembèène 2004


Could fix this here, like this, but I am going to fix in pandas

In [19]:
for mov in list_of_movies:
    if re.search(r".+\d{4}",mov[2]):
        mov[1] = mov[1]+" "+mov[2].split(" ")[0]
        print(mov[1])
        mov[2] = mov[2].split(" ")[1]
        print(mov[2])

Ousmane Sembèène
2004


If you made it this far, yay!


And now, let's bring that into PANDAS!

In [20]:
import numpy as np
import pandas as pd
col_names = ['movie', 'director', 'm_year', 'critic','crit_org','crit_cn']
df = pd.DataFrame.from_records(list_of_movies, columns=col_names)

In [21]:
df

movie                           director m_year  \
0           Mulholland Drive                        David Lynch   2001   
1       In the Mood for Love                       Wong Kar-wai   2000   
2           The Tree of Life                    Terrence Malick   2011   
3     Yi Yi: A One and a Two                        Edward Yang   2000   
4        Goodbye to Language                    Jean-Luc Godard   2014   
...                      ...                                ...    ...   
1765     The Lives of Others   Florian Henckel von Donnersmarck   2006   
1766              Still Life                        Jia Zhangke   2006   
1767                 Birdman        Alejandro González Iñárritu   2014   
1768        Infernal Affairs            Andrew Lau and Alan Mak   2002   
1769             City of God  Fernando Meirelles and Kátia Lund   2002   

            critic               crit_org crit_cn  
0     Simon Abrams  Freelance film critic      US  
1     Simon Abrams  Freelance film critic      US  
2     Simon Abrams  Freelance film critic      US  
3     Simon Abrams  Freelance film critic      US  
4     Simon Abrams  Freelance film critic      US  
...            ...                    ...     ...  
1765  Raymond Zhou            China Daily   China  
1766  Raymond Zhou            China Daily   China  
1767  Raymond Zhou            China Daily   China  
1768  Raymond Zhou            China Daily   China  
1769  Raymond Zhou            China Daily   China  

[1770 rows x 6 columns]

In [22]:
#most popular films
df['movie'].value_counts().head(15)

movie
In the Mood for Love                     49
Mulholland Drive                         47
There Will Be Blood                      35
Spirited Away                            34
Boyhood                                  30
Eternal Sunshine of the Spotless Mind    29
A Separation                             28
The Tree of Life                         23
Yi Yi: A One and a Two                   22
No Country For Old Men                   21
Inside Llewyn Davis                      20
Children of Men                          18
4 Months, 3 Weeks & 2 Days               17
Pan's Labyrinth                          17
The Act of Killing                       16
Name: count, dtype: int64

In [23]:
m_count = df['movie'].value_counts()
m_count[m_count<10]

movie
The Dark Knight                                9
Certified Copy                                 9
Margaret                                       9
Uncle Boonmee Who Can Recall His Past Lives    9
Timbuktu                                       9
                                              ..
Story of My Death                              1
Stranger by the Lake                           1
Even If She Had Been a Criminal...             1
Heart of a Dog                                 1
Lust, Caution                                  1
Name: count, Length: 561, dtype: int64

In [24]:
#critics per country!
df.groupby('crit_cn')['critic'].nunique()

crit_cn
Argentina        2
Australia        4
Austria          2
Bangladesh       1
Belgium          1
Brazil           1
Canada           5
Chile            2
China            1
Colombia         4
Cuba             5
Egypt            1
France           5
Germany          5
Hong Kong        1
India            5
Indonesia        1
Israel           4
Italy            4
Japan            1
Kazakhstan       1
Lebanon          3
Mexico           2
Namibia          1
Philippines      1
Qatar            1
Senegal          1
Singapore        2
South Africa     1
South Korea      2
Switzerland      1
Taiwan           1
Turkey           2
UAE              3
UK              18
US              82
Name: critic, dtype: int64

In [25]:
#back up your results!!!
df.to_csv(r'backup_BBC1.csv', index = False)

In [26]:
df_new = pd.read_csv("backup_BBC1.csv")

In [27]:
d_list = list(df_new['director'].unique())
d_list.sort()
d_list

['Abbas Kiarostami',
 'Abdellatif Kechiche',
 'Abderrahmane Sissako',
 'Adam Curtis',
 'Adam McKay',
 'Agnieszka Holland',
 'Agnès Jaoui',
 'Agnès Varda',
 'Aki Kaurismäki',
 'Alain Cavalier',
 'Alain Gomis',
 'Alain Guiraudie',
 'Alain Resnais',
 'Albert Serra',
 'Alejandro González Iñárritu',
 'Aleksandr Sokurov',
 'Aleksey Fedorchenko',
 'Aleksey German',
 'Alex Garland',
 'Alexander Payne',
 'Alfonso Cuarón',
 'Amma Asante',
 'Ana Lily Amirpour',
 'Andrea Arnold',
 'Andrew Adamson and Vicky Jenson',
 'Andrew Dominik',
 'Andrew Dosunmu',
 'Andrew Haigh',
 'Andrew Lau and Alan Mak',
 'Andrew Stanton',
 'Andrew Stanton and Lee Unkrich',
 'Andrey Zvyagintsev',
 'Andrzej Wajda',
 'Andrzej Zulawski',
 'André Singer',
 'Ang Lee',
 'Annemarie Jacir',
 'Anthony and Joe Russo',
 'Anurag Kashyap',
 'Apichatpong Weerasethakul',
 'Ari Folman',
 'Arnaud Desplechin',
 'Asghar Farhadi',
 'Ashutosh Gowariker',
 'Asif Kapadia',
 'Ava DuVernay',
 'Avi Nesher',
 'Bahman Ghobadi',
 'Bart Layton',
 'Baz

**Getting the names separated**

In [28]:
pd.set_option('display.max_rows', None)
df_new[df_new['director'].str.contains(r"\band\b",regex=True, case=False)]

movie  \
50                               No Country For Old Men   
54                                         Finding Nemo   
60                           These Encounters of Theirs   
68                                                Terra   
69                                              Oh! Man   
77                                  Inside Llewyn Davis   
86                                        A Serious Man   
103                                         City of God   
108                              No Country For Old Men   
133                                     This Is the End   
137                                 Inside Llewyn Davis   
142                                           Anomalisa   
144                  Madagascar 3: Europe's Most Wanted   
185                                          Manakamana   
189                                       A Serious Man   
203                                           The Child   
204                              No Country For Old Men   
226                                   Heaven Knows What   
232                              No Country For Old Men   
236                                             The Son   
242                          O Brother, Where Art Thou?   
256                                         City of God   
260                                 Inside Llewyn Davis   
261                                          Persepolis   
273                                         Ratatouille   
287                                             The Son   
300                              No Country For Old Men   
337                                         City of God   
365                                 Inside Llewyn Davis   
378                               The Five Obstructions   
396                                            Sembène!   
397                                    5 Broken Cameras   
399                                           7 Letters   
407                                   American Splendor   
430                                 Inside Llewyn Davis   
461                                 Inside Llewyn Davis   
466                                              Frozen   
489                                       A Serious Man   
557                                  This Is Not a Film   
570                              Werckmeister Harmonies   
583                                 Inside Llewyn Davis   
585                                     The Turin Horse   
602                                     The Turin Horse   
646                                 Inside Llewyn Davis   
690                                       A Serious Man   
691                                 Inside Llewyn Davis   
704                              No Country For Old Men   
719                                        Finding Nemo   
734                                 Inside Llewyn Davis   
749                                               Ajami   
757                              No Country For Old Men   
788                                     The Turin Horse   
807                                       A Serious Man   
809                                             The Son   
849                                         City of God   
852                                 Inside Llewyn Davis   
906                                             The Son   
912                                 Inside Llewyn Davis   
926                              No Country For Old Men   
928                                         Ratatouille   
931                              No Country For Old Men   
978                                           The Child   
998                          O Brother, Where Art Thou?   
1015                                        City of God   
1020                             No Country For Old Men   
1035                                              Crank   
1039                                            The Son   
1046                             No Co

And this lambda to function, just sends each cell (director) to the dirs_names() function.

Note that here I am testing to make sure the function is working, I'm not saving this work yet.

In [29]:
df_new['director'].value_counts().head(15)

director
Paul Thomas Anderson    52
Joel and Ethan Coen     52
Wong Kar-wai            51
David Lynch             48
Richard Linklater       39
Michael Haneke          35
Hayao Miyazaki          35
Terrence Malick         32
Asghar Farhadi          31
David Fincher           31
Michel Gondry           30
Wes Anderson            28
Christopher Nolan       28
Alfonso Cuarón          24
Edward Yang             22
Name: count, dtype: int64

In [30]:
import re
def dirs_names(dirs):
    each_word = re.split(r"\s+",dirs)
    if len(each_word) > 1 and each_word[1] == "and":
        each_word[0] = each_word[0] + " " + each_word[-1]
        print(' '.join(each_word))
        return ' '.join(each_word)
    else:
        return dirs
        

In [31]:
df_new['director'].apply(lambda x: dirs_names(x))

Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Josh Safdie and Benny Safdie
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Darden

0                                             David Lynch
1                                            Wong Kar-wai
2                                         Terrence Malick
3                                             Edward Yang
4                                         Jean-Luc Godard
5                                       Mohammad Rasoulof
6                                              Raoul Ruiz
7                                        Abbas Kiarostami
8                                              Johnnie To
9                                            Carlos Saura
10                                           Wong Kar-wai
11                                          Michel Gondry
12                              Apichatpong Weerasethakul
13                                         Hayao Miyazaki
14                                     Joshua Oppenheimer
15                                           Wes Anderson
16                                        Terrence Malick
17            

Looking for directors with a single name because that function is assuming that it is always First Name "and"

In [32]:
df_new[df_new['director'].str.contains(r"^\S+$",regex=True, case=False)]

Empty DataFrame
Columns: [movie, director, m_year, critic, crit_org, crit_cn]
Index: []

Oh-oh, problem! Let's fix!

In [33]:
df_new["director"].iat[172] = df_new["director"].iat[172] + " " + df_new["m_year"].iat[172].split(" ")[0]

AttributeError: 'numpy.int64' object has no attribute 'split'

In [34]:
df_new["director"].iat[172]

'Ousmane Sembèène'

In [35]:
df_new["m_year"].iat[172] = df_new["m_year"].iat[172].split(" ")[1]

AttributeError: 'numpy.int64' object has no attribute 'split'

In [36]:
df_new["m_year"].iat[172]

2004

In [37]:
df_new[df_new['director'].str.contains(r"\bOusmane\b",regex=True, case=False)]


movie          director  m_year                 critic  \
172   Moolaadé  Ousmane Sembèène    2004      Lizelle Bisschoff   
190   Moolaadé   Ousmane Sembène    2004          Mahen Bonetti   
395   Moolaadé   Ousmane Sembène    2004          Lindiwe Dovey   
1010  Moolaadé   Ousmane Sembène    2004  Hans-Christian Mahnke   
1536  Moolaadé   Ousmane Sembène    2004              Yael Shuv   

                       crit_org  crit_cn  
172       University of Glasgow       UK  
190   African Film Festival Inc       US  
395        University of London       UK  
1010            AfricAvenir.org  Namibia  
1536          Time Out Tel Aviv   Israel

In [38]:
Whaaatttt???

SyntaxError: invalid syntax (1854124894.py, line 1)

In [39]:
df_new['director'] = df_new['director'].str.replace('Sembèène','Sembène')


In [40]:
df_new[df_new['director'].str.contains(r"\bOusmane\b",regex=True, case=False)]


movie         director  m_year                 critic  \
172   Moolaadé  Ousmane Sembène    2004      Lizelle Bisschoff   
190   Moolaadé  Ousmane Sembène    2004          Mahen Bonetti   
395   Moolaadé  Ousmane Sembène    2004          Lindiwe Dovey   
1010  Moolaadé  Ousmane Sembène    2004  Hans-Christian Mahnke   
1536  Moolaadé  Ousmane Sembène    2004              Yael Shuv   

                       crit_org  crit_cn  
172       University of Glasgow       UK  
190   African Film Festival Inc       US  
395        University of London       UK  
1010            AfricAvenir.org  Namibia  
1536          Time Out Tel Aviv   Israel

**Okay...**

So after that tangent, I'm gonna go ahead and update the directors!!

Here I am saving the work, updating the director column.


In [41]:
df_new['director']=df_new['director'].apply(lambda x: dirs_names(x))

Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Josh Safdie and Benny Safdie
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Dardenne and Luc Dardenne
Joel Coen and Ethan Coen
Joel Coen and Ethan Coen
Jean-Pierre Darden

And checking to make sure it came out, right!

In [42]:
df_new[df_new['director'].str.contains(r"\bCoen\b",regex=True, case=False)]


movie                  director  m_year  \
50        No Country For Old Men  Joel Coen and Ethan Coen    2007   
77           Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
86                 A Serious Man  Joel Coen and Ethan Coen    2009   
108       No Country For Old Men  Joel Coen and Ethan Coen    2007   
137          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
189                A Serious Man  Joel Coen and Ethan Coen    2009   
204       No Country For Old Men  Joel Coen and Ethan Coen    2007   
232       No Country For Old Men  Joel Coen and Ethan Coen    2007   
242   O Brother, Where Art Thou?  Joel Coen and Ethan Coen    2000   
260          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
300       No Country For Old Men  Joel Coen and Ethan Coen    2007   
365          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
430          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
461          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
489                A Serious Man  Joel Coen and Ethan Coen    2009   
583          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
646          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
690                A Serious Man  Joel Coen and Ethan Coen    2009   
691          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
704       No Country For Old Men  Joel Coen and Ethan Coen    2007   
734          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
757       No Country For Old Men  Joel Coen and Ethan Coen    2007   
807                A Serious Man  Joel Coen and Ethan Coen    2009   
852          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
912          Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
926       No Country For Old Men  Joel Coen and Ethan Coen    2007   
931       No Country For Old Men  Joel Coen and Ethan Coen    2007   
998   O Brother, Where Art Thou?  Joel Coen and Ethan Coen    2000   
1020      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1046      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1061      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1106               A Serious Man  Joel Coen and Ethan Coen    2009   
1140         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1197      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1206               A Serious Man  Joel Coen and Ethan Coen    2009   
1209  O Brother, Where Art Thou?  Joel Coen and Ethan Coen    2000   
1283         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1311         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1347         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1382      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1429               A Serious Man  Joel Coen and Ethan Coen    2009   
1440         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1498      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1545         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1558         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1569         Inside Llewyn Davis  Joel Coen and Ethan Coen    2013   
1571      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1598      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1645      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1672      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1719      No Country For Old Men  Joel Coen and Ethan Coen    2007   
1720      No Country For Old Men  Joel Coen and Ethan Coen    2007   

                  critic                         crit_org      crit_cn  
50            Tim Appelo                         The Wrap           US  
77      Michael Arbeiter                          Nerdist           US  
86            Ali Arikan                        Dipnot TV       Turkey  
108    Ana Maria Bahiana

Now I need to deal with multiple directors by looking for commas.

In [43]:
df_new[df_new['director'].str.contains(r",\s+",regex=True, case=False)]


movie  \
144   Madagascar 3: Europe's Most Wanted   
399                            7 Letters   
1396                      Monsters, Inc.   

                                               director  m_year  \
144         Eric Darnell, Tom McGrath and Conrad Vernon    2012   
399   Boo Junfeng, Eric Khoo, Jack Neo, K. Rajagopal...    2015   
1396       Pete Docter, David Silverman and Lee Unkrich    2001   

               critic               crit_org crit_cn  
144   Nicholas Barber            BBC Culture      UK  
399     Lindiwe Dovey   University of London      UK  
1396  Jonathan Romney  Freelance film critic      UK

In [44]:
#beware of oxford commas!!!!
df_new[df_new['director'].str.contains(r",\s+\band\b",regex=True, case=False)]

Empty DataFrame
Columns: [movie, director, m_year, critic, crit_org, crit_cn]
Index: []

Replacing all the commas with ' and ' so that I have a consistent separator for every multiple director cell.

In [45]:
df_new['director']=df_new['director'].str.replace(r",\s+",' and ',regex=True)

In [46]:
df_new[df_new['director'].str.contains(r"\bUnkrich\b",regex=True, case=False)]


movie                                         director  m_year  \
54      Finding Nemo                   Andrew Stanton and Lee Unkrich    2003   
126      Toy Story 3                                      Lee Unkrich    2010   
495      Toy Story 3                                      Lee Unkrich    2010   
719     Finding Nemo                   Andrew Stanton and Lee Unkrich    2003   
1343    Finding Nemo                   Andrew Stanton and Lee Unkrich    2003   
1396  Monsters, Inc.  Pete Docter and David Silverman and Lee Unkrich    2001   
1567     Toy Story 3                                      Lee Unkrich    2010   

                 critic               crit_org    crit_cn  
54           Tim Appelo               The Wrap         US  
126       Lindsay Baker            BBC Culture         UK  
495   Javier Porta Fouz              La Nacion  Argentina  
719        Ann Hornaday    The Washington Post         US  
1343          Sam Rigby            BBC Culture         UK  
1396    Jonathan Romney  Freelance film critic         UK  
1567      Eric D Snider  Freelance film critic         US

In [47]:
df_new['director'].apply(lambda x: len(re.findall(r'\band\b',x))+1)

0       1
1       1
2       1
3       1
4       1
5       1
6       1
7       1
8       1
9       1
10      1
11      1
12      1
13      1
14      1
15      1
16      1
17      1
18      1
19      1
20      1
21      1
22      1
23      1
24      1
25      1
26      1
27      1
28      1
29      1
30      1
31      1
32      1
33      1
34      1
35      1
36      1
37      1
38      1
39      1
40      1
41      1
42      1
43      1
44      1
45      1
46      1
47      1
48      1
49      1
50      2
51      1
52      1
53      1
54      2
55      1
56      1
57      1
58      1
59      1
60      2
61      1
62      1
63      1
64      1
65      1
66      1
67      1
68      2
69      2
70      1
71      1
72      1
73      1
74      1
75      1
76      1
77      2
78      1
79      1
80      1
81      1
82      1
83      1
84      1
85      1
86      2
87      1
88      1
89      1
90      1
91      1
92      1
93      1
94      1
95      1
96      1
97      1
98      1
99      1


Now I am transforming the Director cells into lists using split

In [48]:
df_new['director']=df_new['director'].str.split(' and ')

In [49]:
df_new.iloc[[1396]]

movie                                     director  m_year  \
1396  Monsters, Inc.  [Pete Docter, David Silverman, Lee Unkrich]    2001   

               critic               crit_org crit_cn  
1396  Jonathan Romney  Freelance film critic      UK

In [50]:
df_new

movie  \
0                                      Mulholland Drive   
1                                  In the Mood for Love   
2                                      The Tree of Life   
3                                Yi Yi: A One and a Two   
4                                   Goodbye to Language   
5                                     The White Meadows   
6                               Night Across the Street   
7                                        Certified Copy   
8                                               Sparrow   
9                                                 Fados   
10                                 In the Mood for Love   
11                Eternal Sunshine of the Spotless Mind   
12                              Syndromes and a Century   
13                                        Spirited Away   
14                                   The Act of Killing   
15                             The Grand Budapest Hotel   
16                                        The New World   
17                                       Certified Copy   
18                                            The World   
19                                             Elephant   
20                                     Zero Dark Thirty   
21                                A History of Violence   
22                             The Grand Budapest Hotel   
23                                      Stories We Tell   
24                                        Casino Royale   
25                Eternal Sunshine of the Spotless Mind   
26                                                 Tabu   
27                                           Snow White   
28                                         Frozen River   
29                                         Gosford Park   
30                                 In the Mood for Love   
31                                     Mulholland Drive   
32                                            Inception   
33                                      Pan's Labyrinth   
34                                                Caché   
35                                          Grizzly Man   
36                           4 Months, 3 Weeks & 2 Days   
37                                          Holy Motors   
38                               The Last of the Unjust   
39                                  There Will Be Blood   
40                                    The Piano Teacher   
41                                             Margaret   
42                                      American Psycho   
43                           4 Months, 3 Weeks & 2 Days   
44                                                Caché   
45                                     Mulholland Drive   
46                                              Lourdes   
47                                             Red Road   
48                                              Boyhood   
49                                          Tony Manero   
50                               No Country For Old Men   
51                                        Spirited Away   
52                                         A Separation   
53                                      Pan's Labyrinth   
54                                         Finding Nemo   
55                                                 Hero   
56                              The Wolf of Wall Street   
57                                               Mother   
58                                 The Bourne Ultimatum   
59                                              Traffic   
60                           These Encounters of Theirs   
61                                              Vincere   
62                                     Le quattro volte   
63                               The Profession of Arms   
64                                 Gostanza da Libbiano   
65    Storia di una donna amata e di un assassino ge...   
66                          At the First Breath of Wind   
67                                    

This is fun...! I can use those lists to count the number of directors for a movie, like, why not?

In [51]:
#make dir numbers

df_new['nm_dir'] = df_new['director'].apply(lambda x: len(x))

In [52]:
df_new[df_new['nm_dir']>2]

movie  \
144   Madagascar 3: Europe's Most Wanted   
399                            7 Letters   
1396                      Monsters, Inc.   

                                               director  m_year  \
144          [Eric Darnell, Tom McGrath, Conrad Vernon]    2012   
399   [Boo Junfeng, Eric Khoo, Jack Neo, K. Rajagopa...    2015   
1396        [Pete Docter, David Silverman, Lee Unkrich]    2001   

               critic               crit_org crit_cn  nm_dir  
144   Nicholas Barber            BBC Culture      UK       3  
399     Lindiwe Dovey   University of London      UK       7  
1396  Jonathan Romney  Freelance film critic      UK       3

But, more importantly, let's use **explode()**

This is why we put the director names into a list. explode() allows us to then take that list and make separate rows for each element in the list. This way we are "unwinding" the multiple directors.

This is making a new data frame that will have more rows.

In [53]:
df_large = df_new.explode('director')

In [54]:
df_large.shape

(1891, 7)

In [55]:
df_large[df_large['director'].str.contains(r"\bCoen\b",regex=True, case=False)]

movie    director  m_year              critic  \
50        No Country For Old Men   Joel Coen    2007          Tim Appelo   
50        No Country For Old Men  Ethan Coen    2007          Tim Appelo   
77           Inside Llewyn Davis   Joel Coen    2013    Michael Arbeiter   
77           Inside Llewyn Davis  Ethan Coen    2013    Michael Arbeiter   
86                 A Serious Man   Joel Coen    2009          Ali Arikan   
86                 A Serious Man  Ethan Coen    2009          Ali Arikan   
108       No Country For Old Men   Joel Coen    2007   Ana Maria Bahiana   
108       No Country For Old Men  Ethan Coen    2007   Ana Maria Bahiana   
137          Inside Llewyn Davis   Joel Coen    2013         Miriam Bale   
137          Inside Llewyn Davis  Ethan Coen    2013         Miriam Bale   
189                A Serious Man   Joel Coen    2009  Christian Blauvelt   
189                A Serious Man  Ethan Coen    2009  Christian Blauvelt   
204       No Country For Old Men   Joel Coen    2007   Andreas Borcholte   
204       No Country For Old Men  Ethan Coen    2007   Andreas Borcholte   
232       No Country For Old Men   Joel Coen    2007        Hannah Brown   
232       No Country For Old Men  Ethan Coen    2007        Hannah Brown   
242   O Brother, Where Art Thou?   Joel Coen    2000     Luke Buckmaster   
242   O Brother, Where Art Thou?  Ethan Coen    2000     Luke Buckmaster   
260          Inside Llewyn Davis   Joel Coen    2013     Monica Castillo   
260          Inside Llewyn Davis  Ethan Coen    2013     Monica Castillo   
300       No Country For Old Men   Joel Coen    2007       Cho Seongyong   
300       No Country For Old Men  Ethan Coen    2007       Cho Seongyong   
365          Inside Llewyn Davis   Joel Coen    2013          Erik Davis   
365          Inside Llewyn Davis  Ethan Coen    2013          Erik Davis   
430          Inside Llewyn Davis   Joel Coen    2013        Kate Erbland   
430          Inside Llewyn Davis  Ethan Coen    2013        Kate Erbland   
461          Inside Llewyn Davis   Joel Coen    2013        Devin Faraci   
461          Inside Llewyn Davis  Ethan Coen    2013        Devin Faraci   
489                A Serious Man   Joel Coen    2009      Scott Feinberg   
489                A Serious Man  Ethan Coen    2009      Scott Feinberg   
583          Inside Llewyn Davis   Joel Coen    2013        Tim Grierson   
583          Inside Llewyn Davis  Ethan Coen    2013        Tim Grierson   
646          Inside Llewyn Davis   Joel Coen    2013           Angie Han   
646          Inside Llewyn Davis  Ethan Coen    2013           Angie Han   
690                A Serious Man   Joel Coen    2009      Jordan Hoffman   
690                A Serious Man  Ethan Coen    2009      Jordan Hoffman   
691          Inside Llewyn Davis   Joel Coen    2013      Jordan Hoffman   
691          Inside Llewyn Davis  Ethan Coen    2013      Jordan Hoffman   
704       No Country For Old Men   Joel Coen    2007       Michael Hogan   
704       No Country For Old Men  Ethan Coen    2007       Michael Hogan   
734          Inside Llewyn Davis   Joel Coen    2013        Peter Howell   
734          Inside Llewyn Davis  Ethan Coen    2013        Peter Howell   
757       No Country For Old Men   Joel Coen    2007         Aysha Iqbal   
757       No Country For Old Men  Ethan Coen    2007         Aysha Iqbal   
807                A Serious Man   Joel Coen    2009          Kent Jones   
807                A Serious Man  Ethan Coen    2009          Kent Jones   
852          Inside Llewyn Davis   Joel Coen    2013         Glenn Kenny   
852          Inside Llewyn Davis  Ethan Coen    2013         Glenn Kenny   
912          Inside Llewyn Davis   Joel Coen    2013       Tomris Laffly   
912          Inside Llewyn Davis  Ethan Coen    2013       Tomris Laffly   
926       No Country For Old Men   Joel Coen    2007    Rebecca Laurence   
926       No Country For Old Men  Ethan Coen    2007    Rebecca Laurence   

Now we can get better aggregations with one director per row.

In [56]:
df_large['director'].value_counts().head(15)

director
Ethan Coen              52
Joel Coen               52
Paul Thomas Anderson    52
Wong Kar-wai            51
David Lynch             48
Richard Linklater       39
Hayao Miyazaki          35
Michael Haneke          35
Terrence Malick         32
Asghar Farhadi          31
David Fincher           31
Michel Gondry           30
Christopher Nolan       28
Wes Anderson            28
Alfonso Cuarón          24
Name: count, dtype: int64

In [57]:
df_large.groupby('movie')['critic'].nunique().sort_values(ascending=False).reset_index(name='count')

movie  count
0                                 In the Mood for Love     49
1                                     Mulholland Drive     47
2                                  There Will Be Blood     35
3                                        Spirited Away     34
4                                              Boyhood     30
5                Eternal Sunshine of the Spotless Mind     29
6                                         A Separation     28
7                                     The Tree of Life     23
8                               Yi Yi: A One and a Two     22
9                               No Country For Old Men     21
10                                 Inside Llewyn Davis     20
11                                     Children of Men     18
12                                     Pan's Labyrinth     17
13                          4 Months, 3 Weeks & 2 Days     17
14                                         Holy Motors     16
15                                  The Act of Killing     16
16                                              Zodiac     15
17                                  Mad Max: Fury Road     14
18                                         Talk to Her     13
19                                               Caché     13
20                                  The Social Network     13
21                                    The White Ribbon     13
22                            The Grand Budapest Hotel     12
23                                 Lost in Translation     12
24                                Synecdoche, New York     12
25                                           25th Hour     12
26                                  Brokeback Mountain     11
27                                              WALL-E     11
28                                              Oldboy     11
29                                             Memento     11
30                                         City of God     10
31                                         Son of Saul     10
32                                Inglourious Basterds     10
33                                          The Master     10
34                                 The Lives of Others     10
35                                           Leviathan     10
36                                    12 Years a Slave     10
37                                            Timbuktu      9
38                                      Certified Copy      9
39                                     The Dark Knight      9
40         Uncle Boonmee Who Can Recall His Past Lives      9
41                                            Margaret      9
42                                                Tabu      8
43                      Crouching Tiger, Hidden Dragon      8
44                                          Inside Out      8
45                                               Amour      8
46                                       A Serious Man      8
47                                       The New World      8
48                        Once Upon a Time in Anatolia      7
49                              Only Lovers Left Alive      7
50                                           A Prophet      7
51                                         Melancholia      7
52                                     Spring Breakers      7
53                                      Under the Skin      7
54                           Blue Is the Warmest Color      7
55                                           Inception      7
56                                The Royal Tenenbaums      7
57                                    The Great Beauty      6
58                               A History of Violence      6
59                                       Moulin Rouge!      6
60                                     The Turin Horse      6
61                                     The Hurt Locker      6
62                                                 Ida      6
63                                     Tropical Malady      6
64                 

In [58]:
Now I can get a much better Director List!

SyntaxError: invalid syntax (37108820.py, line 1)

In [59]:
d_list = list(df_large['director'].unique())
d_list.sort()
d_list

['Abbas Kiarostami',
 'Abdellatif Kechiche',
 'Abderrahmane Sissako',
 'Adam Curtis',
 'Adam McKay',
 'Agnieszka Holland',
 'Agnès Jaoui',
 'Agnès Varda',
 'Aki Kaurismäki',
 'Alain Cavalier',
 'Alain Gomis',
 'Alain Guiraudie',
 'Alain Resnais',
 'Alan Mak',
 'Albert Serra',
 'Alejandro González Iñárritu',
 'Aleksandr Sokurov',
 'Aleksey Fedorchenko',
 'Aleksey German',
 'Alex Garland',
 'Alexander Payne',
 'Alfonso Cuarón',
 'Amma Asante',
 'Ana Lily Amirpour',
 'Andrea Arnold',
 'Andrew Adamson',
 'Andrew Dominik',
 'Andrew Dosunmu',
 'Andrew Haigh',
 'Andrew Lau',
 'Andrew Stanton',
 'Andrey Zvyagintsev',
 'Andrzej Wajda',
 'Andrzej Zulawski',
 'André Singer',
 'Ang Lee',
 'Angela Ricci Lucchi',
 'Annemarie Jacir',
 'Anthony Russo',
 'Antonio Di Trapani',
 'Anurag Kashyap',
 'Apichatpong Weerasethakul',
 'Ari Folman',
 'Arnaud Desplechin',
 'Asghar Farhadi',
 'Ashutosh Gowariker',
 'Asif Kapadia',
 'Ava DuVernay',
 'Avi Nesher',
 'Bahman Ghobadi',
 'Bart Layton',
 'Baz Luhrmann',
 

## NEXT STEP

Getting more data!!

In [ ]:
url = "https://www.imdb.com/search/name/?name=David%20Lynch"
#add headers to request
raw_html = requests.get(url).content
print(raw_html)

In [89]:
for director in d_list[:10]:
    url = "https://www.imdb.com/search/name/?name=" + director.replace(" ","%20")
    print(url)

https://www.imdb.com/search/name/?name=Abbas%20Kiarostami
https://www.imdb.com/search/name/?name=Abdellatif%20Kechiche
https://www.imdb.com/search/name/?name=Abderrahmane%20Sissako
https://www.imdb.com/search/name/?name=Adam%20Curtis
https://www.imdb.com/search/name/?name=Adam%20McKay
https://www.imdb.com/search/name/?name=Agnieszka%20Holland
https://www.imdb.com/search/name/?name=Agnès%20Jaoui
https://www.imdb.com/search/name/?name=Agnès%20Varda
https://www.imdb.com/search/name/?name=Aki%20Kaurismäki
https://www.imdb.com/search/name/?name=Alain%20Cavalier


In [ ]:
# {"director":"David Lynch","link":"/name/nm0000186/?ref_=sr_t_1"}
# https://www.imdb.com/name/nm0000186/?ref_=sr_t_1

In [ ]:
#step 1: loop through director list and search for the link
#get a list of dictionaries (table) with just name and link to imdb page

In [ ]:
#step 2: loop through that list of dicts 
#going to each individual and page adding to the dict

In [90]:
raw_html = requests.get(url).content
raw_html

b'<html>\r\n<head><title>403 Forbidden</title></head>\r\n<body>\r\n<center><h1>403 Forbidden</h1></center>\r\n</body>\r\n</html>\r\n'

Getting more Director Info from IMDB

In [60]:
#tell imdb you are using a browser!!
head={'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/102.0.0.0 Safari/537.36'}
#possible urls to use
# url ="https://www.imdb.com/search/title/?name=spirited%20away&title_type=feature"
url = "https://www.imdb.com/search/name/?name=David%20Lynch"
#add headers to request
raw_html = requests.get(url,headers=head).content
#save html file
with open('imdb.html', 'wb+') as f:
    f.write(raw_html)
soup_doc = BeautifulSoup(raw_html, "html.parser")
raw_html


b'<!DOCTYPE html><html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><meta charSet="utf-8"/><meta name="viewport" content="width=device-width"/><script>if(typeof uet === \'function\'){ uet(\'bb\', \'LoadTitle\', {wb: 1}); }</script><script>window.addEventListener(\'load\', (event) => {\n        if (typeof window.csa !== \'undefined\' && typeof window.csa === \'function\') {\n            var csaLatencyPlugin = window.csa(\'Content\', {\n                element: {\n                    slotId: \'LoadTitle\',\n                    type: \'service-call\'\n                }\n            });\n            csaLatencyPlugin(\'mark\', \'clickToBodyBegin\', 1733996328198);\n        }\n    })</script><title>Advanced search</title><meta name="description" content="" data-id="main"/><meta property="og:url" content="https://www.imdb.com/search/"/><meta property="og:site_name" content="IMDb"/><meta property="og:title" content="Advanced se

In [61]:
for director in d_list:
    url = "https://www.imdb.com/search/name/?name=" + director.replace(" ","%20")
    print(url)

https://www.imdb.com/search/name/?name=Abbas%20Kiarostami
https://www.imdb.com/search/name/?name=Abdellatif%20Kechiche
https://www.imdb.com/search/name/?name=Abderrahmane%20Sissako
https://www.imdb.com/search/name/?name=Adam%20Curtis
https://www.imdb.com/search/name/?name=Adam%20McKay
https://www.imdb.com/search/name/?name=Agnieszka%20Holland
https://www.imdb.com/search/name/?name=Agnès%20Jaoui
https://www.imdb.com/search/name/?name=Agnès%20Varda
https://www.imdb.com/search/name/?name=Aki%20Kaurismäki
https://www.imdb.com/search/name/?name=Alain%20Cavalier
https://www.imdb.com/search/name/?name=Alain%20Gomis
https://www.imdb.com/search/name/?name=Alain%20Guiraudie
https://www.imdb.com/search/name/?name=Alain%20Resnais
https://www.imdb.com/search/name/?name=Alan%20Mak
https://www.imdb.com/search/name/?name=Albert%20Serra
https://www.imdb.com/search/name/?name=Alejandro%20González%20Iñárritu
https://www.imdb.com/search/name/?name=Aleksandr%20Sokurov
https://www.imdb.com/search/name/?name

In [62]:
directors_info = []

for director in d_list:
    url = "https://www.imdb.com/search/name/?name=" + director.replace(" ", "%20")
    
    director_info = {
        "name": director,
        "imdb_link": url
    }
    
    directors_info.append(director_info)

for director in directors_info:
    print(director)


{'name': 'Abbas Kiarostami', 'imdb_link': 'https://www.imdb.com/search/name/?name=Abbas%20Kiarostami'}
{'name': 'Abdellatif Kechiche', 'imdb_link': 'https://www.imdb.com/search/name/?name=Abdellatif%20Kechiche'}
{'name': 'Abderrahmane Sissako', 'imdb_link': 'https://www.imdb.com/search/name/?name=Abderrahmane%20Sissako'}
{'name': 'Adam Curtis', 'imdb_link': 'https://www.imdb.com/search/name/?name=Adam%20Curtis'}
{'name': 'Adam McKay', 'imdb_link': 'https://www.imdb.com/search/name/?name=Adam%20McKay'}
{'name': 'Agnieszka Holland', 'imdb_link': 'https://www.imdb.com/search/name/?name=Agnieszka%20Holland'}
{'name': 'Agnès Jaoui', 'imdb_link': 'https://www.imdb.com/search/name/?name=Agnès%20Jaoui'}
{'name': 'Agnès Varda', 'imdb_link': 'https://www.imdb.com/search/name/?name=Agnès%20Varda'}
{'name': 'Aki Kaurismäki', 'imdb_link': 'https://www.imdb.com/search/name/?name=Aki%20Kaurismäki'}
{'name': 'Alain Cavalier', 'imdb_link': 'https://www.imdb.com/search/name/?name=Alain%20Cavalier'}
{'na

In [63]:
# head={'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/102.0.0.0 Safari/537.36'}
# url = "https://www.imdb.com/name/nm0000186/?ref_=sr_t_1"
# raw_html1 = requests.get(url,headers=head).content
# with open('imdb.html', 'wb+') as f:
#     f.write(raw_html1)
# soup_doc = BeautifulSoup(raw_html1, "html.parser")
# raw_html1


b'<!DOCTYPE html><html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><meta charSet="utf-8"/><meta name="viewport" content="width=device-width"/><script>if(typeof uet === \'function\'){ uet(\'bb\', \'LoadTitle\', {wb: 1}); }</script><script>window.addEventListener(\'load\', (event) => {\n        if (typeof window.csa !== \'undefined\' && typeof window.csa === \'function\') {\n            var csaLatencyPlugin = window.csa(\'Content\', {\n                element: {\n                    slotId: \'LoadTitle\',\n                    type: \'service-call\'\n                }\n            });\n            csaLatencyPlugin(\'mark\', \'clickToBodyBegin\', 1733996336312);\n        }\n    })</script><title>David Lynch - IMDb</title><meta name="description" content="David Lynch. Writer: Twin Peaks. Born in precisely the kind of small-town American setting so familiar from his films, David Lynch spent his childhood being shunted from o

In [64]:
# link_tag = soup_doc.find('link', rel='alternate')

# if link_tag:
#     profile_url = link_tag.get('href') 
#     print(profile_url)

https://www.imdb.com/name/nm0000186/


In [65]:
# profile_urls = []

# # Parse the raw HTML only once
# soup_doc = BeautifulSoup(raw_html1, "html.parser")

# # Find the <link> tag with rel="alternate"
# link_tag = soup_doc.find('link', rel='alternate')

# # If the link tag is found, extract the 'href' attribute (the profile URL)
# if link_tag:
#     profile_url = link_tag.get('href')
#     profile_urls.append(profile_url)

# # Print all extracted profile URLs
# for url in profile_urls:
#     print(url)

https://www.imdb.com/name/nm0000186/


In [74]:
import numpy as np
import pandas as pd


df = pd.DataFrame(directors_info)
df


name  \
0                    Abbas Kiarostami   
1                 Abdellatif Kechiche   
2                Abderrahmane Sissako   
3                         Adam Curtis   
4                          Adam McKay   
5                   Agnieszka Holland   
6                         Agnès Jaoui   
7                         Agnès Varda   
8                      Aki Kaurismäki   
9                      Alain Cavalier   
10                        Alain Gomis   
11                    Alain Guiraudie   
12                      Alain Resnais   
13                           Alan Mak   
14                       Albert Serra   
15        Alejandro González Iñárritu   
16                  Aleksandr Sokurov   
17                Aleksey Fedorchenko   
18                     Aleksey German   
19                       Alex Garland   
20                    Alexander Payne   
21                     Alfonso Cuarón   
22                        Amma Asante   
23                  Ana Lily Amirpour   
24                      Andrea Arnold   
25                     Andrew Adamson   
26                     Andrew Dominik   
27                     Andrew Dosunmu   
28                       Andrew Haigh   
29                         Andrew Lau   
30                     Andrew Stanton   
31                 Andrey Zvyagintsev   
32                      Andrzej Wajda   
33                   Andrzej Zulawski   
34                       André Singer   
35                            Ang Lee   
36                Angela Ricci Lucchi   
37                    Annemarie Jacir   
38                      Anthony Russo   
39                 Antonio Di Trapani   
40                     Anurag Kashyap   
41          Apichatpong Weerasethakul   
42                         Ari Folman   
43                  Arnaud Desplechin   
44                     Asghar Farhadi   
45                 Ashutosh Gowariker   
46                       Asif Kapadia   
47                       Ava DuVernay   
48                         Avi Nesher   
49                     Bahman Ghobadi   
50                        Bart Layton   
51                       Baz Luhrmann   
52                          Bazi Gete   
53                         Ben Rivers   
54                        Ben Stiller   
55                       Ben Wheatley   
56                       Benh Zeitlin   
57                       Benny Safdie   
58                       Bong Joon-ho   
59                        Boo Junfeng   
60                      Bouli Lanners   
61                          Brad Bird   
62                     Brian De Palma   
63                       Brian Taylor   
64                          Béla Tarr   
65                      Cameron Crowe   
66                    Carlos Reygadas   
67                       Carlos Saura   
68                       Carol Morley   
69                 Cary Joji Fukunaga   
70                 Catherine Breillat   
71                  Chaitanya Tamhane   
72                    Chantal Akerman   
73                    Charles Burnett   
74                    Charlie Kaufman   
75                         Chris Buck   
76                  Christian Marclay   
77                  Christian Petzold   
78                  Christopher Guest   
79                 Christopher Morris   
80                  Christopher Nolan   
81                       Claire Denis   
82                    Claude Lanzmann   
83                     Clint Eastwood   
84                       Clio Barnard   
85                      Conrad Vernon   
86                 Corneliu Porumboiu   
87                      Courtney Hunt   
88                        Cristi Puiu   
89                    Cristian Mungiu   
90                     Céline Sciamma   
91                    Damien Chazelle   
92                     Damián Szifrón   
93                         Dan Gilroy   
94                      Danis Tanovic   
95                    Danièle Huillet   
96                   Darren Aronofsky   
97             

In [75]:
df.shape

(441, 2)